# Imports and definitions

In [1]:
from pathlib import Path

import polars as pl
import numpy as np

import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots

from sklearn.metrics import (
    accuracy_score, precision_score, recall_score, f1_score,
    roc_auc_score, precision_recall_curve, roc_curve, auc,
    confusion_matrix, classification_report, matthews_corrcoef
)

from sklearn.ensemble import RandomForestClassifier, HistGradientBoostingClassifier
import xgboost as xgb
import lightgbm as lgb
from catboost import CatBoostClassifier

import optuna

_ = pl.Config.set_tbl_cols(None)
_ = pl.Config.set_fmt_str_lengths(500)
_ = pl.Config.set_fmt_float("full")

In [2]:
import warnings
warnings.filterwarnings('ignore', category=RuntimeWarning, module='sklearn')

In [ ]:
base_dir = Path('/workspaces/data-scientist-at-magenta')
code_dir = base_dir / 'notebooks'
data_dir = code_dir / "data"
features_dir = data_dir / 'features'
train_dir = data_dir / 'train'
test_dir = data_dir / 'test'
db_dir = 'sqlite:///data/models/{}.db'

In [4]:
def evaluate_classification_model(y_true, y_pred, y_proba=None,
                                  model_name="Model", pos_label=1,
                                  plot_results=True, print_result=True):
    """
    Comprehensive evaluation function for classification models.

    Parameters:
    -----------
    y_true : Polars Series or array-like
        True labels
    y_pred : Polars Series or array-like
        Predicted labels
    y_proba : Polars Series or array-like, optional
        Predicted probabilities for positive class
    model_name : str
        Name of the model for reporting
    pos_label : int or str
        Label of positive class
    plot_results : bool
        Whether to generate plots
    bootstrap_ci : bool
        Whether to compute bootstrap confidence intervals
    n_bootstrap : int
        Number of bootstrap samples
    confidence_level : float
        Confidence level for intervals

    Returns:
    --------
    dict : Dictionary containing all evaluation metrics
    """

    y_true_np = y_true.to_numpy()
    y_pred_np = y_pred.to_numpy() 
    y_proba_np = y_proba.to_numpy()

    results = {'model_name': model_name}

    results['accuracy'] = accuracy_score(y_true_np, y_pred_np)
    results['precision'] = precision_score(y_true_np, y_pred_np, pos_label=pos_label, average='binary')
    results['recall'] = recall_score(y_true_np, y_pred_np, pos_label=pos_label, average='binary')
    results['f1_score'] = f1_score(y_true_np, y_pred_np, pos_label=pos_label, average='binary')
    results['matthews_corr'] = matthews_corrcoef(y_true_np, y_pred_np)

    cm = confusion_matrix(y_true_np, y_pred_np)
    results['confusion_matrix'] = cm
    results['tn'], results['fp'], results['fn'], results['tp'] = cm.ravel()

    if y_proba_np is not None:
        results['roc_auc'] = roc_auc_score(y_true_np, y_proba_np)
        results['pr_auc'] = auc(*precision_recall_curve(y_true_np, y_proba_np)[:2][::-1])

    # Generate plots
    if plot_results:
        plot_evaluation_results(y_true_np, y_pred_np, y_proba_np, model_name, results)

    if print_result:
        print_evaluation_summary(results)

    return results


def plot_evaluation_results(y_true, y_pred, y_proba, model_name, results):
    """Generate comprehensive evaluation plots using Plotly."""
    figures = []

    # Confusion Matrix
    cm = results['confusion_matrix']
    fig_cm = go.Figure(data=go.Heatmap(
        z=cm,
        x=['Predicted 0', 'Predicted 1'],
        y=['Actual 0', 'Actual 1'],
        colorscale='Blues',
        text=cm,
        texttemplate="%{text}",
        textfont={"size": 20}
    ))
    fig_cm.update_layout(
        title=f'Confusion Matrix: {model_name}',
        xaxis_title='Predicted',
        yaxis_title='Actual',
        xaxis_showgrid=False,
        yaxis_showgrid=False,
        height=400, width=500
    )
    figures.append(fig_cm)

    # Classification Report as heatmap
    report_dict = classification_report(y_true, y_pred, output_dict=True)
    selected_classes = [key for key in report_dict if key not in ['accuracy', 'macro avg', 'weighted avg']]
    report_data = {
        'Metric': ['precision', 'recall', 'f1-score']
    }
    for cls in selected_classes:
        report_data[cls] = [
            report_dict[cls]['precision'],
            report_dict[cls]['recall'],
            report_dict[cls]['f1-score']
        ]

    df_report = pl.DataFrame(report_data)
    report_index = ['precision', 'recall', 'f1-score']
    df_report = df_report.with_columns(
        pl.Series("Metric", report_index).alias("Metric")
    )
    df_report = df_report.select(pl.col("Metric"), pl.exclude("Metric"))

    for col in df_report.columns:
        if col != "Metric":
            df_report = df_report.with_columns(pl.col(col).cast(pl.Float64))

    z_data = df_report.drop("Metric").to_numpy()
    x_labels = df_report.drop("Metric").columns
    y_labels = df_report["Metric"].to_list()

    fig_cr = go.Figure(data=go.Heatmap(
        z=z_data,
        x=x_labels,
        y=y_labels,
        colorscale='RdYlBu_r',
        text=np.around(z_data, decimals=3),
        texttemplate="%{text}",
        textfont={"size": 14}
    ))
    fig_cr.update_layout(
        title=f'Classification Report: {model_name}',
        xaxis_title='Class',
        yaxis_title='Metric',
        xaxis_showgrid=False,
        yaxis_showgrid=False,
        height=400, width=600
    )
    figures.append(fig_cr)

    if y_proba is not None:
        # ROC Curve
        fpr, tpr, _ = roc_curve(y_true, y_proba)
        fig_roc = go.Figure()
        fig_roc.add_trace(go.Scatter(x=fpr, y=tpr, mode='lines',
                                     name=f'ROC (AUC = {results["roc_auc"]:.3f})',
                                     line=dict(width=2)))
        fig_roc.add_trace(go.Scatter(x=[0, 1], y=[0, 1], mode='lines',
                                     name='Random Classifier',
                                     line=dict(dash='dash', color='grey')))
        fig_roc.update_layout(
            title=f'ROC Curve: {model_name}',
            xaxis_title='False Positive Rate',
            yaxis_title='True Positive Rate',
            hovermode='x unified',
            height=450, width=600
        )
        figures.append(fig_roc)

        # Precision-Recall Curve
        precision, recall, _ = precision_recall_curve(y_true, y_proba)
        fig_pr = go.Figure()
        fig_pr.add_trace(go.Scatter(x=recall, y=precision, mode='lines',
                                    name=f'PR (AUC = {results["pr_auc"]:.3f})',
                                    line=dict(width=2)))
        fig_pr.add_trace(go.Scatter(x=[0, 1], y=[np.mean(y_true), np.mean(y_true)], mode='lines',
                                    name='Baseline',
                                    line=dict(dash='dash', color='grey')))
        fig_pr.update_layout(
            title=f'Precision-Recall Curve: {model_name}',
            xaxis_title='Recall',
            yaxis_title='Precision',
            hovermode='x unified',
            height=450, width=600
        )
        figures.append(fig_pr)

        # Prediction Distribution
        fig_dist = go.Figure()
        fig_dist.add_trace(go.Histogram(x=y_proba[y_true == 0], name='Negative Class',
                                        marker_color='red', opacity=0.6, histnorm='probability density'))
        fig_dist.add_trace(go.Histogram(x=y_proba[y_true == 1], name='Positive Class',
                                        marker_color='blue', opacity=0.6, histnorm='probability density'))
        fig_dist.update_layout(
            title=f'Prediction Distribution: {model_name}',
            xaxis_title='Predicted Probability',
            yaxis_title='Density',
            barmode='overlay',
            hovermode='x unified',
            height=450, width=600
        )
        figures.append(fig_dist)

    for fig in figures:
        fig.show()

    return figures

def print_evaluation_summary(results):
    """Print a formatted summary of evaluation results."""
    print(f"\n{'='*60}")
    print(f"EVALUATION SUMMARY: {results['model_name']}")
    print(f"{'='*60}")

    print(f"\nCORE METRICS:")
    print(f"  Accuracy:      {results['accuracy']:.4f}")
    print(f"  Precision:     {results['precision']:.4f}")
    print(f"  Recall:        {results['recall']:.4f}")
    print(f"  F1 Score:      {results['f1_score']:.4f}")
    print(f"  Matthews CC:   {results['matthews_corr']:.4f}")

    if 'roc_auc' in results:
        print(f"\nPROBABILITY-BASED METRICS:")
        print(f"  ROC AUC:       {results['roc_auc']:.4f}")
        print(f"  PR AUC:        {results['pr_auc']:.4f}")

    print(f"\nCONFUSION MATRIX:")
    print(f"  TN: {results['tn']:>6} | FP: {results['fp']:>6}")
    print(f"  FN: {results['fn']:>6} | TP: {results['tp']:>6}")
    

def compare_models(models_results):
    """Compare multiple models and return a comparison DataFrame."""
    comparison_data = []

    for result in models_results:
        row = {
            'Model': result['model_name'],
            'Accuracy': result['accuracy'],
            'Precision': result['precision'],
            'Recall': result['recall'],
            'F1': result['f1_score'],
            'Matthews_CC': result['matthews_corr']
        }

        if 'roc_auc' in result:
            row.update({
                'ROC_AUC': result['roc_auc'],
                'PR_AUC': result['pr_auc']
            })

        comparison_data.append(row)

    comparison_df = pl.DataFrame(comparison_data)
    float_cols = [col for col, dtype in comparison_df.schema.items() if dtype == pl.Float64]
    comparison_df = comparison_df.with_columns([
        pl.col(col).round(4) for col in float_cols
    ])
    return comparison_df

In [5]:
def plot_model_scores(data):
    """
    Plot model scores (XGBoost, CatBoost, RandomForest, LightGBM, HistGradientBoosting) as lines and correctness as colored markers.

    Args:
        data (pl.DataFrame): DataFrame with columns ['xgb_score', 'cat_score', 'rf_score', 'lgb_score', 'hgb_score', 'xgb_pred', 'cat_pred', 'rf_pred', 'lgb_pred', 'hgb__pred'].
    """

    x = data.with_row_index()["index"].to_numpy()
    # Try to get label column, fallback to 'label' if present, else None
    label = data["label"].to_numpy() if "label" in data.columns else None

    def get_colors(pred_col):
        preds = data[pred_col].to_numpy()
        return np.where(preds == label, "green", "red")

    fig = make_subplots(
        rows=5, cols=1, shared_xaxes=True,
        subplot_titles=[
            "XGBoost Score", "CatBoost Score", "RandomForest Score", "LightGBM Score", "HistGradientBoosting Score"
        ]
    )

    # XGBoost
    fig.add_trace(
        go.Scatter(
            x=x,
            y=data["xgb_score"].to_numpy(),
            mode='lines',
            name='XGBoost Line',
            line=dict(color='royalblue'),
            showlegend=True
        ),
        row=1, col=1
    )
    fig.add_trace(
        go.Scatter(
            x=x,
            y=data["xgb_score"].to_numpy(),
            mode='markers',
            marker=dict(color=get_colors("xgb_pred")),
            name='XGBoost Correct/Incorrect',
            hovertemplate="index: %{x}<br>score: %{y:.3f}<br>label: %{customdata}",
            customdata=label,
            showlegend=True
        ),
        row=1, col=1
    )

    # CatBoost
    fig.add_trace(
        go.Scatter(
            x=x,
            y=data["cat_score"].to_numpy(),
            mode='lines',
            name='CatBoost Line',
            line=dict(color='orange'),
            showlegend=True
        ),
        row=2, col=1
    )
    fig.add_trace(
        go.Scatter(
            x=x,
            y=data["cat_score"].to_numpy(),
            mode='markers',
            marker=dict(color=get_colors("cat_pred")),
            name='CatBoost Correct/Incorrect',
            hovertemplate="index: %{x}<br>score: %{y:.3f}<br>label: %{customdata}",
            customdata=label,
            showlegend=True
        ),
        row=2, col=1
    )

    # RandomForest
    fig.add_trace(
        go.Scatter(
            x=x,
            y=data["rf_score"].to_numpy(),
            mode='lines',
            name='RandomForest Line',
            line=dict(color='green'),
            showlegend=True
        ),
        row=3, col=1
    )
    fig.add_trace(
        go.Scatter(
            x=x,
            y=data["rf_score"].to_numpy(),
            mode='markers',
            marker=dict(color=get_colors("rf_pred")),
            name='RandomForest Correct/Incorrect',
            hovertemplate="index: %{x}<br>score: %{y:.3f}<br>label: %{customdata}",
            customdata=label,
            showlegend=True
        ),
        row=3, col=1
    )

    # LightGBM
    fig.add_trace(
        go.Scatter(
            x=x,
            y=data["lgb_score"].to_numpy(),
            mode='lines',
            name='LightGBM Line',
            line=dict(color='purple'),
            showlegend=True
        ),
        row=4, col=1
    )
    fig.add_trace(
        go.Scatter(
            x=x,
            y=data["lgb_score"].to_numpy(),
            mode='markers',
            marker=dict(color=get_colors("lgb_pred")),
            name='LightGBM Correct/Incorrect',
            hovertemplate="index: %{x}<br>score: %{y:.3f}<br>label: %{customdata}",
            customdata=label,
            showlegend=True
        ),
        row=4, col=1
    )

    # HistGradientBoosting
    fig.add_trace(
        go.Scatter(
            x=x,
            y=data["hgb_score"].to_numpy() if "hgb_score" in data.columns else data["hgb__score"].to_numpy(),
            mode='lines',
            name='HistGradientBoosting Line',
            line=dict(color='#FFA15A'),
            showlegend=True
        ),
        row=5, col=1
    )
    fig.add_trace(
        go.Scatter(
            x=x,
            y=data["hgb_score"].to_numpy() if "hgb_score" in data.columns else data["hgb__score"].to_numpy(),
            mode='markers',
            marker=dict(color=get_colors("hgb__pred")),
            name='HistGradientBoosting Correct/Incorrect',
            hovertemplate="index: %{x}<br>score: %{y:.3f}<br>label: %{customdata}",
            customdata=label,
            showlegend=True
        ),
        row=5, col=1
    )

    fig.update_layout(height=1500, width=1600, title_text="Model Scores: Line + Correctness Scatter")
    fig.show()

# Load data

In [6]:
%%time

train = pl.read_parquet(train_dir / 'data-v0-80.parquet')

CPU times: user 13 ms, sys: 6.74 ms, total: 19.8 ms
Wall time: 18.3 ms


In [7]:
%%time

test = pl.read_parquet(test_dir / 'data-v0-20.parquet')

CPU times: user 4.28 ms, sys: 2.25 ms, total: 6.52 ms
Wall time: 6.68 ms


# Prepare data

In [8]:
age_b_1 = train.filter(pl.col("age") < 55).drop('age')
age_b_2 = train.filter(pl.col("age") >= 55).drop('age')

In [9]:
X_train_b1 = age_b_1.select(pl.exclude(['rating_account_id', 'customer_id', 'has_done_upselling']))
X_train_b2 = age_b_2.select(pl.exclude(['rating_account_id', 'customer_id', 'has_done_upselling']))

y_train_b1 = age_b_1.select('has_done_upselling')
y_train_b2 = age_b_2.select('has_done_upselling')


In [10]:
# Testing on hold out test for b1 and b2

X_b1 = test.filter(pl.col("age") < 55).drop('age').select(pl.exclude(['rating_account_id', 'customer_id', 'has_done_upselling']))
y_b1 = test.filter(pl.col("age") < 55).drop('age').select('has_done_upselling')

X_b2 = test.filter(pl.col("age") >= 55).drop('age').select(pl.exclude(['rating_account_id', 'customer_id', 'has_done_upselling']))
y_b2 = test.filter(pl.col("age") >= 55).drop('age').select('has_done_upselling')

In [11]:
X_np_b1 = X_train_b1.to_numpy()
y_np_b1 = y_train_b1.to_numpy().ravel()

X_np_b2 = X_train_b2.to_numpy()
y_np_b2 = y_train_b2.to_numpy().ravel()

# For b1
y_true_np_b1 = y_train_b1.to_numpy().ravel()
# For b2
y_true_np_b2 = y_train_b2.to_numpy().ravel()

# Evaluation

## XGBoost

In [12]:
xgb_study_b1 = optuna.load_study(study_name="xgboost_optimization_age_b_1", storage=db_dir.format('xgb_study'))

b1_xgb_params = xgb_study_b1.best_params
b1_xgb_threshold = xgb_study_b1.best_trial.user_attrs.get('threshold', None)

xgb_model_b1 = xgb.XGBClassifier(**b1_xgb_params,)
xgb_model_b1.fit(X_np_b1, y_np_b1)


XGBClassifier(alpha=2.443988741260388e-08, base_score=None, booster='dart',
              callbacks=None, colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.6634667101281074, device=None,
              early_stopping_rounds=None, enable_categorical=False,
              eta=0.009310315006680062, eval_metric=None, feature_types=None,
              feature_weights=None, gamma=2.0644076081618415e-06,
              grow_policy='lossguide', importance_type=None,
              interaction_constraints=None, lambda=1.070284287482838e-06,
              learning_rate=0.2175665539990347, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=3, max_leaves=None,
              min_child_weight=4, missing=nan, monotone_constraints=None,
              multi_strategy=None, ...)

In [13]:
# Classification with best threshold

print(f"Best XGBoost mean threshold: {b1_xgb_threshold}")
y_proba_np = xgb_model_b1.predict_proba(X_b1.to_numpy())[:, 1]
y_pred_np = (y_proba_np > b1_xgb_threshold).astype(int)

y_true_pl = pl.Series("y_true", y_b1.to_numpy().ravel())
y_pred_pl = pl.Series("y_pred", y_pred_np)
y_proba_pl = pl.Series("y_proba", y_proba_np)

# Evaluate a single model
print("Evaluating XGBoost Model (b1):")
results_xgboost_b1 = evaluate_classification_model(
    y_true=y_true_pl,
    y_pred=y_pred_pl,
    y_proba=y_proba_pl,
    model_name="XGBoost (b1)",
    plot_results=True,
    print_result=True
)


Best XGBoost mean threshold: 0.1413174092769623
Evaluating XGBoost Model (b1):



EVALUATION SUMMARY: XGBoost (b1)

CORE METRICS:
  Accuracy:      0.6677
  Precision:     0.0926
  Recall:        0.4048
  F1 Score:      0.1508
  Matthews CC:   0.0519

PROBABILITY-BASED METRICS:
  ROC AUC:       0.5671
  PR AUC:        0.0911

CONFUSION MATRIX:
  TN:  11358 | FP:   5143
  FN:    772 | TP:    525


In [14]:
xgb_study_b2 = optuna.load_study(study_name="xgboost_optimization_age_b_2", storage=db_dir.format('xgb_study'))

b2_xgb_params = xgb_study_b2.best_params
b2_xgb_threshold = xgb_study_b2.best_trial.user_attrs.get('threshold', None)

xgb_model_b2 = xgb.XGBClassifier(n_jobs=-1, **b2_xgb_params,)
xgb_model_b2.fit(X_np_b2, y_np_b2)


XGBClassifier(alpha=0.10642542092168038, base_score=None, booster='dart',
              callbacks=None, colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.7564539530008034, device=None,
              early_stopping_rounds=None, enable_categorical=False,
              eta=0.027726198358198426, eval_metric=None, feature_types=None,
              feature_weights=None, gamma=2.6629265976902274e-06,
              grow_policy='lossguide', importance_type=None,
              interaction_constraints=None, lambda=0.018561231411393802,
              learning_rate=0.001207184183290601, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=5, max_leaves=None,
              min_child_weight=4, missing=nan, monotone_constraints=None,
              multi_strategy=None, ...)

In [15]:
# Classification with best threshold

print(f"Best XGBoost mean threshold: {b2_xgb_threshold}")
y_proba_np = xgb_model_b2.predict_proba(X_b2.to_numpy())[:, 1]
y_pred_np = (y_proba_np > b2_xgb_threshold).astype(int)

y_true_pl = pl.Series("y_true", y_b2.to_numpy().ravel())
y_pred_pl = pl.Series("y_pred", y_pred_np)
y_proba_pl = pl.Series("y_proba", y_proba_np)

# Evaluate a single model
print("Evaluating XGBoost Model (b2):")
results_xgboost_b2 = evaluate_classification_model(
    y_true=y_true_pl,
    y_pred=y_pred_pl,
    y_proba=y_proba_pl,
    model_name="XGBoost (b2)",
    plot_results=True,
    print_result=True
)


Best XGBoost mean threshold: 0.44614397883415224
Evaluating XGBoost Model (b2):



EVALUATION SUMMARY: XGBoost (b2)

CORE METRICS:
  Accuracy:      0.7443
  Precision:     0.0849
  Recall:        0.4071
  F1 Score:      0.1405
  Matthews CC:   0.0869

PROBABILITY-BASED METRICS:
  ROC AUC:       0.6222
  PR AUC:        0.0764

CONFUSION MATRIX:
  TN:   1593 | FP:    496
  FN:     67 | TP:     46


---

## Catboost

In [16]:
cat_study_b1 = optuna.load_study(study_name="catboost_optimization_age_b_1", storage=db_dir.format('cat_study'))

b1_cat_params = cat_study_b1.best_params
b1_cat_threshold = cat_study_b1.best_trial.user_attrs.get('threshold', None)

cat_model_b1 = CatBoostClassifier(**b1_cat_params, verbose=0)
cat_model_b1.fit(X_np_b1, y_np_b1)


In [17]:
# Classification with best threshold for CatBoost (b1)

print(f"Best CatBoost mean threshold: {b1_cat_threshold}")

y_proba_np = cat_model_b1.predict_proba(X_b1.to_numpy())[:, 1]
y_pred_np = (y_proba_np > b1_cat_threshold).astype(int)

y_true_pl = pl.Series("y_true", y_b1.to_numpy().ravel())
y_pred_pl = pl.Series("y_pred", y_pred_np)
y_proba_pl = pl.Series("y_proba", y_proba_np)

# Evaluate a single model
print("Evaluating CatBoost Model (b1):")
results_catboost_b1 = evaluate_classification_model(
    y_true=y_true_pl,
    y_pred=y_pred_pl,
    y_proba=y_proba_pl,
    model_name="CatBoost (b1)",
    plot_results=True,
    print_result=True
)


Best CatBoost mean threshold: 0.5757361864519136
Evaluating CatBoost Model (b1):



EVALUATION SUMMARY: CatBoost (b1)

CORE METRICS:
  Accuracy:      0.4586
  Precision:     0.0867
  Recall:        0.6739
  F1 Score:      0.1536
  Matthews CC:   0.0606

PROBABILITY-BASED METRICS:
  ROC AUC:       0.5828
  PR AUC:        0.0962

CONFUSION MATRIX:
  TN:   7289 | FP:   9212
  FN:    423 | TP:    874


In [18]:
cat_study_b2 = optuna.load_study(study_name="catboost_optimization_age_b_2", storage=db_dir.format('cat_study'))

b2_cat_params = cat_study_b2.best_params
b2_cat_threshold = cat_study_b2.best_trial.user_attrs.get('threshold', None)

cat_model_b2 = CatBoostClassifier(**b2_cat_params, verbose=0)
cat_model_b2.fit(X_np_b2, y_np_b2)


In [19]:
# Classification with best threshold for CatBoost (b2)

print(f"Best CatBoost mean threshold: {b2_cat_threshold}")

y_proba_np = cat_model_b2.predict_proba(X_b2.to_numpy())[:, 1]
y_pred_np = (y_proba_np > b2_cat_threshold).astype(int)

y_true_pl = pl.Series("y_true", y_b2.to_numpy().ravel())
y_pred_pl = pl.Series("y_pred", y_pred_np)
y_proba_pl = pl.Series("y_proba", y_proba_np)

# Evaluate a single model
print("Evaluating CatBoost Model (b2):")
results_catboost_b2 = evaluate_classification_model(
    y_true=y_true_pl,
    y_pred=y_pred_pl,
    y_proba=y_proba_pl,
    model_name="CatBoost (b2)",
    plot_results=True,
    print_result=True
)


Best CatBoost mean threshold: 0.536969537393525
Evaluating CatBoost Model (b2):



EVALUATION SUMMARY: CatBoost (b2)

CORE METRICS:
  Accuracy:      0.9373
  Precision:     0.0370
  Recall:        0.0088
  F1 Score:      0.0143
  Matthews CC:   -0.0072

PROBABILITY-BASED METRICS:
  ROC AUC:       0.5937
  PR AUC:        0.0673

CONFUSION MATRIX:
  TN:   2063 | FP:     26
  FN:    112 | TP:      1


---

## LightGBM

In [20]:
lgb_study_b1 = optuna.load_study(study_name="lightgbm_optimization_age_b_1", storage=db_dir.format('lgb_study'))

b1_lgb_params = lgb_study_b1.best_params
b1_lgb_threshold = lgb_study_b1.best_trial.user_attrs.get('threshold', None)

lgb_model_b1 = lgb.LGBMClassifier(**b1_lgb_params)
lgb_model_b1.fit(X_np_b1, y_np_b1)


[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] feature_fraction is set=0.7733869325685215, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7733869325685215
[LightGBM] [Warning] bagging_fraction is set=0.9067648273393395, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9067648273393395
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] feature_fraction is set=0.7733869325685215, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7733869325685215
[LightGBM] [Warning] bagging_fraction is set=0.9067648273393395, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9067648273393395
[LightGBM] [Info] Number of positive: 5176, number of negative: 65995
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004118 seconds.
You can 

LGBMClassifier(bagging_fraction=0.9067648273393395, bagging_freq=5,
               feature_fraction=0.7733869325685215,
               learning_rate=0.2020132088190523, min_child_samples=93,
               num_leaves=21, reg_alpha=0.7516042979209725,
               reg_lambda=0.44094257157114747,
               scale_pos_weight=13.871420499157374)

In [21]:
# Classification with best threshold for LightGBM (b1)

print(f"Best LightGBM mean threshold: {b1_lgb_threshold}")

y_proba_np = lgb_model_b1.predict_proba(X_b1.to_numpy())[:, 1]
y_pred_np = (y_proba_np > b1_lgb_threshold).astype(int)

y_true_pl = pl.Series("y_true", y_b1.to_numpy().ravel())
y_pred_pl = pl.Series("y_pred", y_pred_np)
y_proba_pl = pl.Series("y_proba", y_proba_np)

# Evaluate a single model
print("Evaluating LightGBM Model (b1):")
results_lgb_b1 = evaluate_classification_model(
    y_true=y_true_pl,
    y_pred=y_pred_pl,
    y_proba=y_proba_pl,
    model_name="LightGBM (b1)",
    plot_results=True,
    print_result=True
)


Best LightGBM mean threshold: 0.2439880193092078
[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] feature_fraction is set=0.7733869325685215, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7733869325685215
[LightGBM] [Warning] bagging_fraction is set=0.9067648273393395, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9067648273393395
Evaluating LightGBM Model (b1):


/Users/danlab/code/magenta-task/.venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names




EVALUATION SUMMARY: LightGBM (b1)

CORE METRICS:
  Accuracy:      0.1497
  Precision:     0.0733
  Recall:        0.9167
  F1 Score:      0.1358
  Matthews CC:   0.0056

PROBABILITY-BASED METRICS:
  ROC AUC:       0.5494
  PR AUC:        0.0881

CONFUSION MATRIX:
  TN:   1476 | FP:  15025
  FN:    108 | TP:   1189


In [22]:
lgb_study_b2 = optuna.load_study(study_name="lightgbm_optimization_age_b_2", storage=db_dir.format('lgb_study'))

b2_lgb_params = lgb_study_b2.best_params
b2_lgb_threshold = lgb_study_b2.best_trial.user_attrs.get('threshold', None)

lgb_model_b2 = lgb.LGBMClassifier(**b2_lgb_params)
lgb_model_b2.fit(X_np_b2, y_np_b2)


[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] feature_fraction is set=0.8174117537984181, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8174117537984181
[LightGBM] [Warning] bagging_fraction is set=0.9629170289938864, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9629170289938864
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] feature_fraction is set=0.8174117537984181, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8174117537984181
[LightGBM] [Warning] bagging_fraction is set=0.9629170289938864, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9629170289938864
[LightGBM] [Info] Number of positive: 463, number of negative: 8366
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001339 seconds.
You can se

LGBMClassifier(bagging_fraction=0.9629170289938864, bagging_freq=4,
               feature_fraction=0.8174117537984181,
               learning_rate=0.21979530795145358, min_child_samples=43,
               num_leaves=80, reg_alpha=0.7755279139054861,
               reg_lambda=0.5791414013058541,
               scale_pos_weight=18.82185801404129)

In [23]:
# Classification with best threshold for LightGBM (b2)

print(f"Best LightGBM mean threshold: {b2_lgb_threshold}")

y_proba_np = lgb_model_b2.predict_proba(X_b2.to_numpy())[:, 1]
y_pred_np = (y_proba_np > b2_lgb_threshold).astype(int)

y_true_pl = pl.Series("y_true", y_b2.to_numpy().ravel())
y_pred_pl = pl.Series("y_pred", y_pred_np)
y_proba_pl = pl.Series("y_proba", y_proba_np)

# Evaluate a single model
print("Evaluating LightGBM Model (b2):")
results_lgb_b2 = evaluate_classification_model(
    y_true=y_true_pl,
    y_pred=y_pred_pl,
    y_proba=y_proba_pl,
    model_name="LightGBM (b2)",
    plot_results=True,
    print_result=True
)


Best LightGBM mean threshold: 0.11748700486982366
[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] feature_fraction is set=0.8174117537984181, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8174117537984181
[LightGBM] [Warning] bagging_fraction is set=0.9629170289938864, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9629170289938864
Evaluating LightGBM Model (b2):


/Users/danlab/code/magenta-task/.venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names




EVALUATION SUMMARY: LightGBM (b2)

CORE METRICS:
  Accuracy:      0.8860
  Precision:     0.0893
  Recall:        0.1327
  F1 Score:      0.1068
  Matthews CC:   0.0495

PROBABILITY-BASED METRICS:
  ROC AUC:       0.5693
  PR AUC:        0.0663

CONFUSION MATRIX:
  TN:   1936 | FP:    153
  FN:     98 | TP:     15


---

## RandomForest

In [24]:
rf_study_b1 = optuna.load_study(study_name="random_forest_optimization_age_b_1", storage=db_dir.format('rf_study'))

b1_rf_params = rf_study_b1.best_params

rf_model_b1 = RandomForestClassifier(**b1_rf_params)
rf_model_b1.fit(X_np_b1, y_np_b1)


RandomForestClassifier(class_weight='balanced', max_depth=6, max_leaf_nodes=138,
                       max_samples=0.23951992376128442, min_samples_leaf=2,
                       min_samples_split=4,
                       min_weight_fraction_leaf=0.0322792826276814,
                       n_estimators=414)

In [25]:
# Classification with best threshold for RandomForest (b1)

# If you have a threshold from Optuna, use it; otherwise, default to 0.5
b1_rf_threshold = 0.5  # Set your threshold here if available

print(f"Best RandomForest mean threshold: {b1_rf_threshold}")

y_proba_np = rf_model_b1.predict_proba(X_b1.to_numpy())[:, 1]
y_pred_np = (y_proba_np > b1_rf_threshold).astype(int)

y_true_pl = pl.Series("y_true", y_b1.to_numpy().ravel())
y_pred_pl = pl.Series("y_pred", y_pred_np)
y_proba_pl = pl.Series("y_proba", y_proba_np)

# Evaluate a single model
print("Evaluating RandomForest Model (b1):")
results_rf_b1 = evaluate_classification_model(
    y_true=y_true_pl,
    y_pred=y_pred_pl,
    y_proba=y_proba_pl,
    model_name="RandomForest (b1)",
    plot_results=True,
    print_result=True
)


Best RandomForest mean threshold: 0.5
Evaluating RandomForest Model (b1):



EVALUATION SUMMARY: RandomForest (b1)

CORE METRICS:
  Accuracy:      0.6070
  Precision:     0.0913
  Recall:        0.4904
  F1 Score:      0.1539
  Matthews CC:   0.0568

PROBABILITY-BASED METRICS:
  ROC AUC:       0.5841
  PR AUC:        0.0969

CONFUSION MATRIX:
  TN:  10168 | FP:   6333
  FN:    661 | TP:    636


In [26]:
rf_study_b2 = optuna.load_study(study_name="random_forest_optimization_age_b_2", storage=db_dir.format('rf_study'))

b2_rf_params = rf_study_b2.best_params

rf_model_b2 = RandomForestClassifier(**b2_rf_params)
rf_model_b2.fit(X_np_b2, y_np_b2)


RandomForestClassifier(class_weight='balanced', max_depth=4, max_leaf_nodes=286,
                       max_samples=0.5017851962691026, min_samples_leaf=3,
                       min_samples_split=5,
                       min_weight_fraction_leaf=0.002546502102164078,
                       n_estimators=931)

In [27]:
# Classification with best threshold for RandomForest (b2)

b2_rf_threshold = 0.5  # Set your threshold here if available

print(f"Best RandomForest mean threshold: {b2_rf_threshold}")

y_proba_np = rf_model_b2.predict_proba(X_b2.to_numpy())[:, 1]
y_pred_np = (y_proba_np > b2_rf_threshold).astype(int)

y_true_pl = pl.Series("y_true", y_b2.to_numpy().ravel())
y_pred_pl = pl.Series("y_pred", y_pred_np)
y_proba_pl = pl.Series("y_proba", y_proba_np)

# Evaluate a single model
print("Evaluating RandomForest Model (b2):")
results_rf_b2 = evaluate_classification_model(
    y_true=y_true_pl,
    y_pred=y_pred_pl,
    y_proba=y_proba_pl,
    model_name="RandomForest (b2)",
    plot_results=True,
    print_result=True
)


Best RandomForest mean threshold: 0.5
Evaluating RandomForest Model (b2):



EVALUATION SUMMARY: RandomForest (b2)

CORE METRICS:
  Accuracy:      0.7493
  Precision:     0.0738
  Recall:        0.3363
  F1 Score:      0.1210
  Matthews CC:   0.0563

PROBABILITY-BASED METRICS:
  ROC AUC:       0.6149
  PR AUC:        0.0718

CONFUSION MATRIX:
  TN:   1612 | FP:    477
  FN:     75 | TP:     38


---

## HistGradientBoost

In [28]:
histgb__study_b1 = optuna.load_study(study_name="histgb_optimization_age_b_1", storage=db_dir.format('histgb_study'))

histgb__xgb_params = histgb__study_b1.best_params
histgb__xgb_threshold = histgb__study_b1.best_trial.user_attrs.get('threshold', None)

histgb__model_b1 = HistGradientBoostingClassifier(**histgb__xgb_params,)
histgb__model_b1.fit(X_np_b1, y_np_b1)


HistGradientBoostingClassifier(l2_regularization=0.25018585110288427,
                               learning_rate=0.09137833371402335, max_bins=173,
                               max_depth=3, max_iter=157, min_samples_leaf=98)

In [29]:
# Classification with best threshold

y_proba_np = histgb__model_b1.predict_proba(X_b1.to_numpy())[:, 1]
y_pred_np = (y_proba_np > histgb__xgb_threshold).astype(int)

y_true_pl = pl.Series("y_true", y_b1.to_numpy().ravel())
y_pred_pl = pl.Series("y_pred", y_pred_np)
y_proba_pl = pl.Series("y_proba", y_proba_np)

# Evaluate a single model
print("Evaluating HistGradientBoost Model (b1):")
results_hgb_b1 = evaluate_classification_model(
    y_true=y_true_pl,
    y_pred=y_pred_pl,
    y_proba=y_proba_pl,
    model_name="HistGradientBoost (b1)",
    plot_results=True,
    print_result=True
)


Evaluating HistGradientBoost Model (b1):



EVALUATION SUMMARY: HistGradientBoost (b1)

CORE METRICS:
  Accuracy:      0.6262
  Precision:     0.0918
  Recall:        0.4641
  F1 Score:      0.1532
  Matthews CC:   0.0555

PROBABILITY-BASED METRICS:
  ROC AUC:       0.5849
  PR AUC:        0.0971

CONFUSION MATRIX:
  TN:  10543 | FP:   5958
  FN:    695 | TP:    602


In [30]:
histgb__study_b2 = optuna.load_study(study_name="histgb_optimization_age_b_2", storage=db_dir.format('histgb_study'))

histgb__xgb_params = histgb__study_b2.best_params
histgb__xgb_threshold = histgb__study_b2.best_trial.user_attrs.get('threshold', None)

histgb__model_b2 = HistGradientBoostingClassifier(**histgb__xgb_params,)
histgb__model_b2.fit(X_np_b2, y_np_b2)


HistGradientBoostingClassifier(l2_regularization=0.25776573696908545,
                               learning_rate=0.2053520596646573, max_bins=123,
                               max_depth=4, max_iter=323, min_samples_leaf=25)

In [31]:
# Classification with best threshold for HistGradientBoost (b2)

y_proba_np = histgb__model_b2.predict_proba(X_b2.to_numpy())[:, 1]
y_pred_np = (y_proba_np > histgb__xgb_threshold).astype(int)

y_true_pl = pl.Series("y_true", y_b2.to_numpy().ravel())
y_pred_pl = pl.Series("y_pred", y_pred_np)
y_proba_pl = pl.Series("y_proba", y_proba_np)

# Evaluate a single model
print("Evaluating HistGradientBoost Model (b2):")
results_hgb_b2 = evaluate_classification_model(
    y_true=y_true_pl,
    y_pred=y_pred_pl,
    y_proba=y_proba_pl,
    model_name="HistGradientBoost (b2)",
    plot_results=True,
    print_result=True
)


Evaluating HistGradientBoost Model (b2):



EVALUATION SUMMARY: HistGradientBoost (b2)

CORE METRICS:
  Accuracy:      0.8556
  Precision:     0.0949
  Recall:        0.2124
  F1 Score:      0.1311
  Matthews CC:   0.0711

PROBABILITY-BASED METRICS:
  ROC AUC:       0.5964
  PR AUC:        0.0675

CONFUSION MATRIX:
  TN:   1860 | FP:    229
  FN:     89 | TP:     24


---

# Performance analysis

In [32]:
# Compare only "b1" model results using the compare_models function
b1_results = [
    results_xgboost_b1,
    results_catboost_b1,
    results_lgb_b1,
    results_rf_b1,
    results_hgb_b1
]

comparison_b1_df = compare_models(b1_results)
comparison_b1_df.sort('F1', descending=True)


shape: (5, 8)
┌────────────────────────┬──────────┬───────────┬────────┬────────┬─────────────┬─────────┬────────┐
│ Model                  ┆ Accuracy ┆ Precision ┆ Recall ┆ F1     ┆ Matthews_CC ┆ ROC_AUC ┆ PR_AUC │
│ ---                    ┆ ---      ┆ ---       ┆ ---    ┆ ---    ┆ ---         ┆ ---     ┆ ---    │
│ str                    ┆ f64      ┆ f64       ┆ f64    ┆ f64    ┆ f64         ┆ f64     ┆ f64    │
╞════════════════════════╪══════════╪═══════════╪════════╪════════╪═════════════╪═════════╪════════╡
│ RandomForest (b1)      ┆ 0.607    ┆ 0.0913    ┆ 0.4904 ┆ 0.1539 ┆ 0.0568      ┆ 0.5841  ┆ 0.0969 │
│ CatBoost (b1)          ┆ 0.4586   ┆ 0.0867    ┆ 0.6739 ┆ 0.1536 ┆ 0.0606      ┆ 0.5828  ┆ 0.0962 │
│ HistGradientBoost (b1) ┆ 0.6262   ┆ 0.0918    ┆ 0.4641 ┆ 0.1532 ┆ 0.0555      ┆ 0.5849  ┆ 0.0971 │
│ XGBoost (b1)           ┆ 0.6677   ┆ 0.0926    ┆ 0.4048 ┆ 0.1508 ┆ 0.0519      ┆ 0.5671  ┆ 0.0911 │
│ LightGBM (b1)          ┆ 0.1497   ┆ 0.0733    ┆ 0.9167 ┆ 0.1358 ┆ 0.0056      ┆ 0.5494  ┆ 0.0881 │
└────────────────────────┴──────────┴───────────┴────────┴────────┴─────────────┴─────────┴────────┘

In [33]:
# Compare only "b2" model results using the compare_models function
b2_results = [
    results_xgboost_b2,
    results_catboost_b2,
    results_lgb_b2,
    results_rf_b2,
    results_hgb_b2
]

comparison_b2_df = compare_models(b2_results)
comparison_b2_df.sort('F1', descending=True)


shape: (5, 8)
┌────────────────────────┬──────────┬───────────┬────────┬────────┬─────────────┬─────────┬────────┐
│ Model                  ┆ Accuracy ┆ Precision ┆ Recall ┆ F1     ┆ Matthews_CC ┆ ROC_AUC ┆ PR_AUC │
│ ---                    ┆ ---      ┆ ---       ┆ ---    ┆ ---    ┆ ---         ┆ ---     ┆ ---    │
│ str                    ┆ f64      ┆ f64       ┆ f64    ┆ f64    ┆ f64         ┆ f64     ┆ f64    │
╞════════════════════════╪══════════╪═══════════╪════════╪════════╪═════════════╪═════════╪════════╡
│ XGBoost (b2)           ┆ 0.7443   ┆ 0.0849    ┆ 0.4071 ┆ 0.1405 ┆ 0.0869      ┆ 0.6222  ┆ 0.0764 │
│ HistGradientBoost (b2) ┆ 0.8556   ┆ 0.0949    ┆ 0.2124 ┆ 0.1311 ┆ 0.0711      ┆ 0.5964  ┆ 0.0675 │
│ RandomForest (b2)      ┆ 0.7493   ┆ 0.0738    ┆ 0.3363 ┆ 0.121  ┆ 0.0563      ┆ 0.6149  ┆ 0.0718 │
│ LightGBM (b2)          ┆ 0.886    ┆ 0.0893    ┆ 0.1327 ┆ 0.1068 ┆ 0.0495      ┆ 0.5693  ┆ 0.0663 │
│ CatBoost (b2)          ┆ 0.9373   ┆ 0.037     ┆ 0.0088 ┆ 0.0143 ┆ -0.0072     ┆ 0.5937  ┆ 0.0673 │
└────────────────────────┴──────────┴───────────┴────────┴────────┴─────────────┴─────────┴────────┘

In [34]:
# Get prediction scores (probabilities) for each model's "b1" configuration on X_b1
lgb_proba_b1 = lgb_model_b1.predict_proba(X_b1.to_numpy())[:, 1]
xgb_proba_b1 = xgb_model_b1.predict_proba(X_b1.to_numpy())[:, 1]
cat_proba_b1 = cat_model_b1.predict_proba(X_b1.to_numpy())[:, 1]
rf_proba_b1 = rf_model_b1.predict_proba(X_b1.to_numpy())[:, 1]
hgb_proba_b1 = histgb__model_b1.predict_proba(X_b1.to_numpy())[:, 1]

# Create a DataFrame with the scores
models_scores_b1 = pl.DataFrame({
    "lgb_score": lgb_proba_b1,
    "xgb_score": xgb_proba_b1,
    "cat_score": cat_proba_b1,
    "rf_score": rf_proba_b1,
    "hgb_score": hgb_proba_b1,
    "label": y_b1.to_numpy().ravel()
})

models_scores_b1 = models_scores_b1.with_columns([
    (pl.col("xgb_score") > b1_xgb_threshold).cast(pl.Int8).alias("xgb_pred"),
    (pl.col("cat_score") > b1_cat_threshold).cast(pl.Int8).alias("cat_pred"),
    (pl.col("lgb_score") > b1_lgb_threshold).cast(pl.Int8).alias("lgb_pred"),
    (pl.col("hgb_score") > histgb__xgb_threshold).cast(pl.Int8).alias("hgb__pred"),
    (pl.col("rf_score") > 0.5).cast(pl.Int8).alias("rf_pred"),
])

[LightGBM] [Warning] bagging_freq is set=5, subsample_freq=0 will be ignored. Current value: bagging_freq=5
[LightGBM] [Warning] feature_fraction is set=0.7733869325685215, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7733869325685215
[LightGBM] [Warning] bagging_fraction is set=0.9067648273393395, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9067648273393395


/Users/danlab/code/magenta-task/.venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names



In [35]:
# Get prediction scores (probabilities) for each model's "b2" configuration on X_b2
lgb_proba_b2 = lgb_model_b2.predict_proba(X_b2.to_numpy())[:, 1]
xgb_proba_b2 = xgb_model_b2.predict_proba(X_b2.to_numpy())[:, 1]
cat_proba_b2 = cat_model_b2.predict_proba(X_b2.to_numpy())[:, 1]
rf_proba_b2 = rf_model_b2.predict_proba(X_b2.to_numpy())[:, 1]
hgb_proba_b2 = histgb__model_b2.predict_proba(X_b2.to_numpy())[:, 1]

# Create a DataFrame with the scores
models_scores_b2 = pl.DataFrame({
    "lgb_score": lgb_proba_b2,
    "xgb_score": xgb_proba_b2,
    "cat_score": cat_proba_b2,
    "rf_score": rf_proba_b2,
    "hgb_score": hgb_proba_b2,
    "label": y_b2.to_numpy().ravel()
})

models_scores_b2 = models_scores_b2.with_columns([
    (pl.col("xgb_score") > b2_xgb_threshold).cast(pl.Int8).alias("xgb_pred"),
    (pl.col("cat_score") > b2_cat_threshold).cast(pl.Int8).alias("cat_pred"),
    (pl.col("lgb_score") > b2_lgb_threshold).cast(pl.Int8).alias("lgb_pred"),
    (pl.col("hgb_score") > histgb__xgb_threshold).cast(pl.Int8).alias("hgb__pred"),
    (pl.col("rf_score") > 0.5).cast(pl.Int8).alias("rf_pred"),
])

/Users/danlab/code/magenta-task/.venv/lib/python3.12/site-packages/sklearn/utils/validation.py:2749: UserWarning:

X does not have valid feature names, but LGBMClassifier was fitted with feature names



[LightGBM] [Warning] bagging_freq is set=4, subsample_freq=0 will be ignored. Current value: bagging_freq=4
[LightGBM] [Warning] feature_fraction is set=0.8174117537984181, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.8174117537984181
[LightGBM] [Warning] bagging_fraction is set=0.9629170289938864, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9629170289938864


### B2

In [36]:
sampled = models_scores_b1.sample(300)

In [37]:
plot_model_scores(sampled)

### B2

In [38]:
sampled = models_scores_b2.sample(300)

In [39]:
plot_model_scores(sampled)

In [40]:
# Compute the correlation matrix of model_scores using Polars
correlation_matrix_b1 = models_scores_b1.select([col for col in models_scores_b1.columns if "_score" in col]).corr()

In [41]:
correlation_matrix_b1

shape: (5, 5)
┌───────────────────┬───────────────────┬───────────────────┬───────────────────┬──────────────────┐
│ lgb_score         ┆ xgb_score         ┆ cat_score         ┆ rf_score          ┆ hgb_score        │
│ ---               ┆ ---               ┆ ---               ┆ ---               ┆ ---              │
│ f64               ┆ f64               ┆ f64               ┆ f64               ┆ f64              │
╞═══════════════════╪═══════════════════╪═══════════════════╪═══════════════════╪══════════════════╡
│ 1                 ┆ 0.660997018037779 ┆ 0.703568586512445 ┆ 0.612519014798045 ┆ 0.65245510894242 │
│                   ┆ 3                 ┆ 2                 ┆ 8                 ┆ 13               │
│ 0.660997018037779 ┆ 1                 ┆ 0.706813464225492 ┆ 0.667430939701569 ┆ 0.71943487275792 │
│ 2                 ┆                   ┆ 7                 ┆                   ┆                  │
│ 0.703568586512445 ┆ 0.706813464225492 ┆ 1                 ┆ 0.874337307154943 ┆ 0.90286161139154 │
│ 2                 ┆ 7                 ┆                   ┆ 1                 ┆ 34               │
│ 0.612519014798045 ┆ 0.667430939701569 ┆ 0.874337307154943 ┆ 0.999999999999999 ┆ 0.90057101323923 │
│ 8                 ┆                   ┆ 1                 ┆ 8                 ┆ 52               │
│ 0.652455108942421 ┆ 0.719434872757919 ┆ 0.902861611391543 ┆ 0.900571013239235 ┆ 1                │
│ 3                 ┆ 8                 ┆ 5                 ┆ 2                 ┆                  │
└───────────────────┴───────────────────┴───────────────────┴───────────────────┴──────────────────┘

In [42]:
fig = px.imshow(
    correlation_matrix_b1.to_numpy(),
    labels=dict(x='Model', y='Model', color='Correlation'),
    x=correlation_matrix_b1.columns,
    y=correlation_matrix_b1.columns,
    color_continuous_scale='RdBu',
    zmin=-1, zmax=1,
    aspect='auto'
)
fig.update_layout(
    width=800,
    height=600,
    title='Correlation Matrix Heatmap'
)
fig.update_layout(title='Correlation Matrix Heatmap')
fig.show()

# Blue means that variable X and variable Y follow the same behaviour (both increasing or decreasing)
# Red means that variable X has the opposite behaviour of variable Y

In [43]:
# Compute the correlation matrix of model_scores using Polars
correlation_matrix_b2 = models_scores_b2.select([col for col in models_scores_b2.columns if "_score" in col]).corr()

In [44]:
correlation_matrix_b2

shape: (5, 5)
┌───────────────────┬───────────────────┬───────────────────┬───────────────────┬──────────────────┐
│ lgb_score         ┆ xgb_score         ┆ cat_score         ┆ rf_score          ┆ hgb_score        │
│ ---               ┆ ---               ┆ ---               ┆ ---               ┆ ---              │
│ f64               ┆ f64               ┆ f64               ┆ f64               ┆ f64              │
╞═══════════════════╪═══════════════════╪═══════════════════╪═══════════════════╪══════════════════╡
│ 1                 ┆ 0.324621904010631 ┆ 0.519944331053717 ┆ 0.246221142888344 ┆ 0.56370860461071 │
│                   ┆ 07                ┆ 1                 ┆ 57                ┆ 15               │
│ 0.324621904010631 ┆ 1                 ┆ 0.561973254538014 ┆ 0.898540637860157 ┆ 0.43570110122795 │
│                   ┆                   ┆ 4                 ┆ 6                 ┆ 874              │
│ 0.519944331053717 ┆ 0.561973254538014 ┆ 0.999999999999999 ┆ 0.455850185522809 ┆ 0.63945993354724 │
│                   ┆ 4                 ┆ 9                 ┆ 26                ┆ 04               │
│ 0.246221142888344 ┆ 0.898540637860157 ┆ 0.455850185522809 ┆ 1                 ┆ 0.33878509336545 │
│ 6                 ┆ 7                 ┆ 2                 ┆                   ┆ 2                │
│ 0.563708604610711 ┆ 0.435701101227958 ┆ 0.639459933547240 ┆ 0.338785093365452 ┆ 1                │
│ 5                 ┆ 8                 ┆ 4                 ┆                   ┆                  │
└───────────────────┴───────────────────┴───────────────────┴───────────────────┴──────────────────┘

In [45]:
fig = px.imshow(
    correlation_matrix_b1.to_numpy(),
    labels=dict(x='Model', y='Model', color='Correlation'),
    x=correlation_matrix_b1.columns,
    y=correlation_matrix_b1.columns,
    color_continuous_scale='RdBu',
    zmin=-1, zmax=1,
    aspect='auto'
)
fig.update_layout(
    width=800,
    height=600,
    title='Correlation Matrix Heatmap'
)
fig.update_layout(title='Correlation Matrix Heatmap')
fig.show()

# Blue means that variable X and variable Y follow the same behaviour (both increasing or decreasing)
# Red means that variable X has the opposite behaviour of variable Y

In [46]:
# For each row, check pairwise agreement/disagreement and the general decision (majority vote), including HistGradientBoosting
opposite_decisions_b1 = models_scores_b1.with_columns([
    (pl.col("xgb_pred") != pl.col("cat_pred")).alias("opposite_decision_xgb_vs_cat"),
    (pl.col("xgb_pred") != pl.col("lgb_pred")).alias("opposite_decision_xgb_vs_lgb"),
    (pl.col("xgb_pred") != pl.col("rf_pred")).alias("opposite_decision_xgb_vs_rf"),
    (pl.col("xgb_pred") != pl.col("hgb__pred")).alias("opposite_decision_xgb_vs_hgb"),
    (pl.col("cat_pred") != pl.col("lgb_pred")).alias("opposite_decision_cat_vs_lgb"),
    (pl.col("cat_pred") != pl.col("rf_pred")).alias("opposite_decision_cat_vs_rf"),
    (pl.col("cat_pred") != pl.col("hgb__pred")).alias("opposite_decision_cat_vs_hgb"),
    (pl.col("lgb_pred") != pl.col("rf_pred")).alias("opposite_decision_lgb_vs_rf"),
    (pl.col("lgb_pred") != pl.col("hgb__pred")).alias("opposite_decision_lgb_vs_hgb"),
    (pl.col("rf_pred") != pl.col("hgb__pred")).alias("opposite_decision_rf_vs_hgb"),
    (pl.sum_horizontal(["xgb_pred", "cat_pred", "lgb_pred", "rf_pred", "hgb__pred"]) >= 3).cast(pl.Int64).alias("majority_vote"),
    y_b1["has_done_upselling"].alias("label")
]).select([
    "label", "xgb_pred", "cat_pred", "lgb_pred", "rf_pred", "hgb__pred",
    "opposite_decision_xgb_vs_cat",
    "opposite_decision_xgb_vs_lgb",
    "opposite_decision_xgb_vs_rf",
    "opposite_decision_xgb_vs_hgb",
    "opposite_decision_cat_vs_lgb",
    "opposite_decision_cat_vs_rf",
    "opposite_decision_cat_vs_hgb",
    "opposite_decision_lgb_vs_rf",
    "opposite_decision_lgb_vs_hgb",
    "opposite_decision_rf_vs_hgb",
    "majority_vote"
])

opposite_decisions_b1

shape: (17_798, 17)
┌───────┬──────────┬──────────┬──────────┬───┬─────────────┬─────────────┬────────────┬────────────┐
│ label ┆ xgb_pred ┆ cat_pred ┆ lgb_pred ┆ … ┆ opposite_de ┆ opposite_de ┆ opposite_d ┆ majority_v │
│ ---   ┆ ---      ┆ ---      ┆ ---      ┆   ┆ cision_lgb_ ┆ cision_lgb_ ┆ ecision_rf ┆ ote        │
│ bool  ┆ i8       ┆ i8       ┆ i8       ┆   ┆ vs_rf       ┆ vs_hgb      ┆ _vs_hgb    ┆ ---        │
│       ┆          ┆          ┆          ┆   ┆ ---         ┆ ---         ┆ ---        ┆ i64        │
│       ┆          ┆          ┆          ┆   ┆ bool        ┆ bool        ┆ bool       ┆            │
╞═══════╪══════════╪══════════╪══════════╪═══╪═════════════╪═════════════╪════════════╪════════════╡
│ true  ┆ 1        ┆ 1        ┆ 1        ┆ … ┆ false       ┆ false       ┆ false      ┆ 1          │
│ false ┆ 0        ┆ 0        ┆ 1        ┆ … ┆ true        ┆ true        ┆ false      ┆ 0          │
│ false ┆ 1        ┆ 1        ┆ 1        ┆ … ┆ false       ┆ false       ┆ false      ┆ 1          │
│ false ┆ 1        ┆ 1        ┆ 1        ┆ … ┆ false       ┆ false       ┆ false      ┆ 1          │
│ false ┆ 0        ┆ 0        ┆ 1        ┆ … ┆ true        ┆ false       ┆ true       ┆ 0          │
│ …     ┆ …        ┆ …        ┆ …        ┆ … ┆ …           ┆ …           ┆ …          ┆ …          │
│ false ┆ 0        ┆ 0        ┆ 0        ┆ … ┆ false       ┆ false       ┆ false      ┆ 0          │
│ false ┆ 0        ┆ 0        ┆ 0        ┆ … ┆ false       ┆ false       ┆ false      ┆ 0          │
│ false ┆ 0        ┆ 0        ┆ 1        ┆ … ┆ true        ┆ true        ┆ false      ┆ 0          │
│ false ┆ 0        ┆ 0        ┆ 1        ┆ … ┆ true        ┆ true        ┆ false      ┆ 0          │
│ false ┆ 0        ┆ 0        ┆ 0        ┆ … ┆ false       ┆ false       ┆ false      ┆ 0          │
└───────┴──────────┴──────────┴──────────┴───┴─────────────┴─────────────┴────────────┴────────────┘

In [47]:
# Count how many times each pair of models give opposite decisions and who is correct in those cases, with percentages
def opposite_decision_stats(preds_df, y_true_col="label"):
    pairs = [
        ("xgb_pred", "cat_pred"),
        ("xgb_pred", "lgb_pred"),
        ("xgb_pred", "rf_pred"),
        ("xgb_pred", "hgb__pred"),
        ("cat_pred", "lgb_pred"),
        ("cat_pred", "rf_pred"),
        ("cat_pred", "hgb__pred"),
        ("lgb_pred", "rf_pred"),
        ("lgb_pred", "hgb__pred"),
        ("rf_pred", "hgb__pred"),
    ]
    n_total = preds_df.height
    stats = []
    for a, b in pairs:
        mask = preds_df[a] != preds_df[b]
        n_opposite = mask.sum()
        correct_a = ((preds_df[a] == preds_df[y_true_col]) & mask).sum()
        correct_b = ((preds_df[b] == preds_df[y_true_col]) & mask).sum()
        stats.append({
            "model_a": a,
            "model_b": b,
            "opposite_count": n_opposite,
            "opposite_pct": round(n_opposite / n_total * 100, 2),
            "model_a_correct": correct_a,
            "model_a_correct_pct": round(correct_a / n_opposite * 100, 2) if n_opposite > 0 else 0,
            "model_b_correct": correct_b,
            "model_b_correct_pct": round(correct_b / n_opposite * 100, 2) if n_opposite > 0 else 0,
        })
    return pl.DataFrame(stats)

opposite_stats_b1 = opposite_decision_stats(opposite_decisions_b1)
opposite_stats_b1

shape: (10, 8)
┌──────────┬───────────┬────────────┬────────────┬────────────┬────────────┬───────────┬───────────┐
│ model_a  ┆ model_b   ┆ opposite_c ┆ opposite_p ┆ model_a_co ┆ model_a_co ┆ model_b_c ┆ model_b_c │
│ ---      ┆ ---       ┆ ount       ┆ ct         ┆ rrect      ┆ rrect_pct  ┆ orrect    ┆ orrect_pc │
│ str      ┆ str       ┆ ---        ┆ ---        ┆ ---        ┆ ---        ┆ ---       ┆ t         │
│          ┆           ┆ i64        ┆ f64        ┆ i64        ┆ f64        ┆ i64       ┆ ---       │
│          ┆           ┆            ┆            ┆            ┆            ┆           ┆ f64       │
╞══════════╪═══════════╪════════════╪════════════╪════════════╪════════════╪═══════════╪═══════════╡
│ xgb_pred ┆ cat_pred  ┆ 5274       ┆ 29.63      ┆ 4497       ┆ 85.27      ┆ 777       ┆ 14.73     │
│ xgb_pred ┆ lgb_pred  ┆ 10634      ┆ 59.75      ┆ 9926       ┆ 93.34      ┆ 708       ┆ 6.66      │
│ xgb_pred ┆ rf_pred   ┆ 3901       ┆ 21.92      ┆ 2490       ┆ 63.83      ┆ 1411      ┆ 36.17     │
│ xgb_pred ┆ hgb__pred ┆ 4811       ┆ 27.03      ┆ 4034       ┆ 83.85      ┆ 777       ┆ 16.15     │
│ cat_pred ┆ lgb_pred  ┆ 6470       ┆ 36.35      ┆ 5984       ┆ 92.49      ┆ 486       ┆ 7.51      │
│ cat_pred ┆ rf_pred   ┆ 3705       ┆ 20.82      ┆ 532        ┆ 14.36      ┆ 3173      ┆ 85.64     │
│ cat_pred ┆ hgb__pred ┆ 1759       ┆ 9.88       ┆ 648        ┆ 36.84      ┆ 1111      ┆ 63.16     │
│ lgb_pred ┆ rf_pred   ┆ 9525       ┆ 53.52      ┆ 693        ┆ 7.28       ┆ 8832      ┆ 92.72     │
│ lgb_pred ┆ hgb__pred ┆ 7083       ┆ 39.8       ┆ 561        ┆ 7.92       ┆ 6522      ┆ 92.08     │
│ rf_pred  ┆ hgb__pred ┆ 3092       ┆ 17.37      ┆ 2635       ┆ 85.22      ┆ 457       ┆ 14.78     │
└──────────┴───────────┴────────────┴────────────┴────────────┴────────────┴───────────┴───────────┘

In [48]:
# For each row, check pairwise agreement/disagreement and the general decision (majority vote), including HistGradientBoosting
opposite_decisions_b2 = models_scores_b2.with_columns([
    (pl.col("xgb_pred") != pl.col("cat_pred")).alias("opposite_decision_xgb_vs_cat"),
    (pl.col("xgb_pred") != pl.col("lgb_pred")).alias("opposite_decision_xgb_vs_lgb"),
    (pl.col("xgb_pred") != pl.col("rf_pred")).alias("opposite_decision_xgb_vs_rf"),
    (pl.col("xgb_pred") != pl.col("hgb__pred")).alias("opposite_decision_xgb_vs_hgb"),
    (pl.col("cat_pred") != pl.col("lgb_pred")).alias("opposite_decision_cat_vs_lgb"),
    (pl.col("cat_pred") != pl.col("rf_pred")).alias("opposite_decision_cat_vs_rf"),
    (pl.col("cat_pred") != pl.col("hgb__pred")).alias("opposite_decision_cat_vs_hgb"),
    (pl.col("lgb_pred") != pl.col("rf_pred")).alias("opposite_decision_lgb_vs_rf"),
    (pl.col("lgb_pred") != pl.col("hgb__pred")).alias("opposite_decision_lgb_vs_hgb"),
    (pl.col("rf_pred") != pl.col("hgb__pred")).alias("opposite_decision_rf_vs_hgb"),
    (pl.sum_horizontal(["xgb_pred", "cat_pred", "lgb_pred", "rf_pred", "hgb__pred"]) >= 3).cast(pl.Int64).alias("majority_vote"),
    y_b2["has_done_upselling"].alias("label")
]).select([
    "label", "xgb_pred", "cat_pred", "lgb_pred", "rf_pred", "hgb__pred",
    "opposite_decision_xgb_vs_cat",
    "opposite_decision_xgb_vs_lgb",
    "opposite_decision_xgb_vs_rf",
    "opposite_decision_xgb_vs_hgb",
    "opposite_decision_cat_vs_lgb",
    "opposite_decision_cat_vs_rf",
    "opposite_decision_cat_vs_hgb",
    "opposite_decision_lgb_vs_rf",
    "opposite_decision_lgb_vs_hgb",
    "opposite_decision_rf_vs_hgb",
    "majority_vote"
])

opposite_decisions_b2

shape: (2_202, 17)
┌───────┬──────────┬──────────┬──────────┬───┬─────────────┬─────────────┬────────────┬────────────┐
│ label ┆ xgb_pred ┆ cat_pred ┆ lgb_pred ┆ … ┆ opposite_de ┆ opposite_de ┆ opposite_d ┆ majority_v │
│ ---   ┆ ---      ┆ ---      ┆ ---      ┆   ┆ cision_lgb_ ┆ cision_lgb_ ┆ ecision_rf ┆ ote        │
│ bool  ┆ i8       ┆ i8       ┆ i8       ┆   ┆ vs_rf       ┆ vs_hgb      ┆ _vs_hgb    ┆ ---        │
│       ┆          ┆          ┆          ┆   ┆ ---         ┆ ---         ┆ ---        ┆ i64        │
│       ┆          ┆          ┆          ┆   ┆ bool        ┆ bool        ┆ bool       ┆            │
╞═══════╪══════════╪══════════╪══════════╪═══╪═════════════╪═════════════╪════════════╪════════════╡
│ false ┆ 0        ┆ 0        ┆ 0        ┆ … ┆ false       ┆ false       ┆ false      ┆ 0          │
│ false ┆ 0        ┆ 0        ┆ 0        ┆ … ┆ false       ┆ false       ┆ false      ┆ 0          │
│ false ┆ 0        ┆ 0        ┆ 0        ┆ … ┆ false       ┆ false       ┆ false      ┆ 0          │
│ false ┆ 0        ┆ 0        ┆ 0        ┆ … ┆ false       ┆ false       ┆ false      ┆ 0          │
│ false ┆ 0        ┆ 0        ┆ 1        ┆ … ┆ true        ┆ true        ┆ false      ┆ 0          │
│ …     ┆ …        ┆ …        ┆ …        ┆ … ┆ …           ┆ …           ┆ …          ┆ …          │
│ false ┆ 0        ┆ 0        ┆ 0        ┆ … ┆ false       ┆ false       ┆ false      ┆ 0          │
│ false ┆ 0        ┆ 0        ┆ 0        ┆ … ┆ false       ┆ false       ┆ false      ┆ 0          │
│ false ┆ 1        ┆ 0        ┆ 0        ┆ … ┆ true        ┆ false       ┆ true       ┆ 0          │
│ false ┆ 0        ┆ 0        ┆ 0        ┆ … ┆ false       ┆ false       ┆ false      ┆ 0          │
│ false ┆ 1        ┆ 0        ┆ 0        ┆ … ┆ true        ┆ false       ┆ true       ┆ 0          │
└───────┴──────────┴──────────┴──────────┴───┴─────────────┴─────────────┴────────────┴────────────┘

In [49]:
# Count how many times each pair of models give opposite decisions and who is correct in those cases, with percentages
def opposite_decision_stats(preds_df, y_true_col="label"):
    pairs = [
        ("xgb_pred", "cat_pred"),
        ("xgb_pred", "lgb_pred"),
        ("xgb_pred", "rf_pred"),
        ("xgb_pred", "hgb__pred"),
        ("cat_pred", "lgb_pred"),
        ("cat_pred", "rf_pred"),
        ("cat_pred", "hgb__pred"),
        ("lgb_pred", "rf_pred"),
        ("lgb_pred", "hgb__pred"),
        ("rf_pred", "hgb__pred"),
    ]
    n_total = preds_df.height
    stats = []
    for a, b in pairs:
        mask = preds_df[a] != preds_df[b]
        n_opposite = mask.sum()
        correct_a = ((preds_df[a] == preds_df[y_true_col]) & mask).sum()
        correct_b = ((preds_df[b] == preds_df[y_true_col]) & mask).sum()
        stats.append({
            "model_a": a,
            "model_b": b,
            "opposite_count": n_opposite,
            "opposite_pct": round(n_opposite / n_total * 100, 2),
            "model_a_correct": correct_a,
            "model_a_correct_pct": round(correct_a / n_opposite * 100, 2) if n_opposite > 0 else 0,
            "model_b_correct": correct_b,
            "model_b_correct_pct": round(correct_b / n_opposite * 100, 2) if n_opposite > 0 else 0,
        })
    return pl.DataFrame(stats)

opposite_stats_b2 = opposite_decision_stats(opposite_decisions_b2)
opposite_stats_b2

shape: (10, 8)
┌──────────┬───────────┬────────────┬────────────┬────────────┬────────────┬───────────┬───────────┐
│ model_a  ┆ model_b   ┆ opposite_c ┆ opposite_p ┆ model_a_co ┆ model_a_co ┆ model_b_c ┆ model_b_c │
│ ---      ┆ ---       ┆ ount       ┆ ct         ┆ rrect      ┆ rrect_pct  ┆ orrect    ┆ orrect_pc │
│ str      ┆ str       ┆ ---        ┆ ---        ┆ ---        ┆ ---        ┆ ---       ┆ t         │
│          ┆           ┆ i64        ┆ f64        ┆ i64        ┆ f64        ┆ i64       ┆ ---       │
│          ┆           ┆            ┆            ┆            ┆            ┆           ┆ f64       │
╞══════════╪═══════════╪════════════╪════════════╪════════════╪════════════╪═══════════╪═══════════╡
│ xgb_pred ┆ cat_pred  ┆ 521        ┆ 23.66      ┆ 48         ┆ 9.21       ┆ 473       ┆ 90.79     │
│ xgb_pred ┆ lgb_pred  ┆ 514        ┆ 23.34      ┆ 101        ┆ 19.65      ┆ 413       ┆ 80.35     │
│ xgb_pred ┆ rf_pred   ┆ 223        ┆ 10.13      ┆ 106        ┆ 47.53      ┆ 117       ┆ 52.47     │
│ xgb_pred ┆ hgb__pred ┆ 465        ┆ 21.12      ┆ 110        ┆ 23.66      ┆ 355       ┆ 76.34     │
│ cat_pred ┆ lgb_pred  ┆ 159        ┆ 7.22       ┆ 136        ┆ 85.53      ┆ 23        ┆ 14.47     │
│ cat_pred ┆ rf_pred   ┆ 502        ┆ 22.8       ┆ 458        ┆ 91.24      ┆ 44        ┆ 8.76      │
│ cat_pred ┆ hgb__pred ┆ 230        ┆ 10.45      ┆ 205        ┆ 89.13      ┆ 25        ┆ 10.87     │
│ lgb_pred ┆ rf_pred   ┆ 519        ┆ 23.57      ┆ 410        ┆ 79         ┆ 109       ┆ 21        │
│ lgb_pred ┆ hgb__pred ┆ 213        ┆ 9.67       ┆ 140        ┆ 65.73      ┆ 73        ┆ 34.27     │
│ rf_pred  ┆ hgb__pred ┆ 484        ┆ 21.98      ┆ 125        ┆ 25.83      ┆ 359       ┆ 74.17     │
└──────────┴───────────┴────────────┴────────────┴────────────┴────────────┴───────────┴───────────┘

looking at this stats catboost and xgboost are a good combination

In [50]:
# TODO: revwrite the message

**Key Insights:**

Random Forest is severely overfitting - Perfect recall (1.0) and precision (1.0) with 0 Matthews Correlation Coefficient suggests it's memorizing the training data rather than learning generalizable patterns.

**CatBoost (base) is actually your best performer:**

- Highest accuracy: 0.8408
- Best balance across metrics
- Reasonable Matthews CC: 0.0294
- Good ROC_AUC: 0.5521


XGBoost (base) is second best with solid balanced performance across metrics.

In [ ]:
import pickle

artifacts_dir = data_dir / 'models/artifacts'
artifacts_dir.mkdir(parents=True, exist_ok=True)

# Save models for b1
with open(artifacts_dir / 'pre_xgb_age_b1.pkl', 'wb') as f:
    pickle.dump(xgb_model_b1, f)
with open(artifacts_dir / 'pre_cat_age_b1.pkl', 'wb') as f:
    pickle.dump(cat_model_b1, f)
with open(artifacts_dir / 'pre_lgb_age_b1.pkl', 'wb') as f:
    pickle.dump(lgb_model_b1, f)
with open(artifacts_dir / 'pre_rf_age_b1.pkl', 'wb') as f:
    pickle.dump(rf_model_b1, f)
with open(artifacts_dir / 'pre_histgb_age_b1.pkl', 'wb') as f:
    pickle.dump(histgb__model_b1, f)

# Save models for b2
with open(artifacts_dir / 'pre_xgb_age_b2.pkl', 'wb') as f:
    pickle.dump(xgb_model_b2, f)
with open(artifacts_dir / 'pre_cat_age_b2.pkl', 'wb') as f:
    pickle.dump(cat_model_b2, f)
with open(artifacts_dir / 'pre_lgb_age_b2.pkl', 'wb') as f:
    pickle.dump(lgb_model_b2, f)
with open(artifacts_dir / 'pre_rf_age_b2.pkl', 'wb') as f:
    pickle.dump(rf_model_b2, f)
with open(artifacts_dir / 'pre_histgb_age_b2.pkl', 'wb') as f:
    pickle.dump(histgb__model_b2, f)